# RESEARCH NOTEBOOK --> XGridT


In [1]:
# This is necessary to recognize the modules
import os
import sys
from decimal import Decimal
import warnings

warnings.filterwarnings("ignore")

root_path = os.path.abspath(os.path.join(os.getcwd(), '../..'))
sys.path.append(root_path)

In [2]:
import pandas as pd
import pandas_ta as ta  # noqa: F401
from core.data_sources import CLOBDataSource

# Initialize the data source
clob = CLOBDataSource()

In [9]:
# Define the parameters
exchange = "binance_perpetual"
trading_pair = "MANTA-USDT"
timeframe = "15m"
days = 120

In [15]:
# Get the candles
candles = await clob.get_candles_last_days(
    exchange, trading_pair, timeframe, days, from_trades=False)
daily_candles = await clob.get_candles_last_days(
    exchange, trading_pair, "1d", days, from_trades=False)


2024-11-16 18:16:07,757 - asyncio - ERROR - Unclosed client session
client_session: <aiohttp.client.ClientSession object at 0x16aacbf70>
2024-11-16 18:16:07,758 - asyncio - ERROR - Unclosed connector
connections: ['[(<aiohttp.client_proto.ResponseHandler object at 0x137aa1240>, 218000.908045166)]']
connector: <aiohttp.connector.TCPConnector object at 0x16aacaec0>
2024-11-16 18:16:09,306 - asyncio - ERROR - Unclosed client session
client_session: <aiohttp.client.ClientSession object at 0x16aacbf70>
2024-11-16 18:16:09,308 - asyncio - ERROR - Unclosed connector
connections: ['[(<aiohttp.client_proto.ResponseHandler object at 0x137aa1240>, 218002.466538666)]']
connector: <aiohttp.connector.TCPConnector object at 0x16aaca950>


In [16]:
candles.data

timestamp   open   high    low  close   volume  \
timestamp                                                             
2024-07-19 21:30:00 1721424600 1.0377 1.0425 1.0377 1.0407 126284.1   
2024-07-19 21:45:00 1721425500 1.0403  1.041 1.0315 1.0322 191124.7   
2024-07-19 22:00:00 1721426400 1.0322 1.0366 1.0322  1.036 173238.2   
2024-07-19 22:15:00 1721427300  1.036 1.0371 1.0324 1.0331 198094.5   
2024-07-19 22:30:00 1721428200 1.0327 1.0349 1.0312 1.0315 189701.3   
...                        ...    ...    ...    ...    ...      ...   
2024-11-16 20:15:00 1731788100 0.8472  0.849 0.8379 0.8382 195355.5   
2024-11-16 20:30:00 1731789000 0.8383 0.8466 0.8383 0.8449   144338   
2024-11-16 20:45:00 1731789900 0.8448 0.8469 0.8386 0.8415   142084   
2024-11-16 21:00:00 1731790800 0.8415   0.85 0.8402 0.8488 211579.9   
2024-11-16 21:15:00 1731791700 0.8488  0.851 0.8486 0.8506    12818   

                     quote_asset_volume  n_trades  taker_buy_base_volume  \
timestamp                                                                  
2024-07-19 21:30:00        131387.71186      1384                74820.2   
2024-07-19 21:45:00        197938.44084      1385                  42556   
2024-07-19 22:00:00        179206.35459      1627                78643.5   
2024-07-19 22:15:00        204978.59138      1376                90332.5   
2024-07-19 22:30:00         195930.8538      1583                60348.9   
...                                 ...       ...                    ...   
2024-11-16 20:15:00        164657.08957      2066                64764.7   
2024-11-16 20:30:00        121624.61819      1781                81422.9   
2024-11-16 20:45:00        119772.82541      1546                66740.8   
2024-11-16 21:00:00        178846.56418      2281               106925.9   
2024-11-16 21:15:00         10895.15296       159                 9161.1   

                     taker_buy_quote_volume  
timestamp                                    
2024-07-19 21:30:00             77845.98572  
2024-07-19 21:45:00             44125.56636  
2024-07-19 22:00:00             81365.41255  
2024-07-19 22:15:00             93525.78752  
2024-07-19 22:30:00             62344.44285  
...                                     ...  
2024-11-16 20:15:00             54588.01891  
2024-11-16 20:30:00              68617.4104  
2024-11-16 20:45:00             56293.17193  
2024-11-16 21:00:00             90443.29911  
2024-11-16 21:15:00              7788.37796  

[11519 rows x 10 columns]

In [17]:
candles.plot(type="candles", width=1800)

In [35]:
from hummingbot.strategy_v2.utils.distributions import Distributions

# EMAs
ema_short = 8
ema_medium = 29
ema_long = 31
take_profit_windows = [int(x) for x in Distributions.arithmetic(start=720, step=720, n_levels=300)]
stop_loss_windows = [int(x) for x in Distributions.arithmetic(start=100, step=100, n_levels=50)]


# ATR
atr_length = 11
atr_multiplier = 1.5

# Add indicators
candles_df = candles.data
candles_df.ta.atr(length=atr_length, append=True)
candles_df.ta.ema(length=ema_short, append=True)
candles_df.ta.ema(length=ema_medium, append=True)
candles_df.ta.ema(length=ema_long, append=True)
for window in take_profit_windows:
    candles_df[f"TP_MAX_{window}"] = candles_df["high"].rolling(window=window).max()
    candles_df[f"TP_MIN_{window}"] = candles_df["low"].rolling(window=window).min()

for window in stop_loss_windows:
    candles_df[f"SL_MAX_{window}"] = candles_df["high"].rolling(window=window).max()
    candles_df[f"SL_MIN_{window}"] = candles_df["low"].rolling(window=window).min()

def get_resistance_tp(row):
    for window in take_profit_windows:
        if row[f"TP_MAX_{window}"] > row["close"]:
            return row[f"TP_MAX_{window}"]
    return None

def get_support_tp(row):
    for window in take_profit_windows:
        if row[f"TP_MIN_{window}"] < row["close"]:
            return row[f"TP_MIN_{window}"]
    return None

def get_resistance_sl(row):
    for window in stop_loss_windows:
        if row[f"SL_MAX_{window}"] > row["close"]:
            return row[f"SL_MAX_{window}"]
    return None

def get_support_sl(row):
    for window in stop_loss_windows:
        if row[f"SL_MIN_{window}"] < row["close"]:
            return row[f"SL_MIN_{window}"]
    return None



candles_df["resistance_tp"] = candles_df.apply(get_resistance_tp, axis=1)
candles_df["support_tp"] = candles_df.apply(get_support_tp, axis=1)
candles_df["resistance_sl"] = candles_df.apply(get_resistance_sl, axis=1)
candles_df["support_sl"] = candles_df.apply(get_support_sl, axis=1)


candles_df["long_atr_support"] = candles_df["close"].shift(1) - candles_df[f"ATRr_{atr_length}"] * atr_multiplier
candles_df["short_atr_resistance"] = candles_df["close"].shift(1) + candles_df[f"ATRr_{atr_length}"] * atr_multiplier

candles_df.tail(5)

timestamp   open   high    low  close   volume  \
timestamp                                                             
2024-11-16 20:15:00 1731788100 0.8472  0.849 0.8379 0.8382 195355.5   
2024-11-16 20:30:00 1731789000 0.8383 0.8466 0.8383 0.8449   144338   
2024-11-16 20:45:00 1731789900 0.8448 0.8469 0.8386 0.8415   142084   
2024-11-16 21:00:00 1731790800 0.8415   0.85 0.8402 0.8488 211579.9   
2024-11-16 21:15:00 1731791700 0.8488  0.851 0.8486 0.8506    12818   

                     quote_asset_volume  n_trades  taker_buy_base_volume  \
timestamp                                                                  
2024-11-16 20:15:00        164657.08957      2066                64764.7   
2024-11-16 20:30:00        121624.61819      1781                81422.9   
2024-11-16 20:45:00        119772.82541      1546                66740.8   
2024-11-16 21:00:00        178846.56418      2281               106925.9   
2024-11-16 21:15:00         10895.15296       159                 9161.1   

                     taker_buy_quote_volume  ...  TP_MAX_141120  \
timestamp                                    ...                  
2024-11-16 20:15:00             54588.01891  ...            NaN   
2024-11-16 20:30:00              68617.4104  ...            NaN   
2024-11-16 20:45:00             56293.17193  ...            NaN   
2024-11-16 21:00:00             90443.29911  ...            NaN   
2024-11-16 21:15:00              7788.37796  ...            NaN   

                     TP_MIN_141120  TP_MAX_141840  TP_MIN_141840  \
timestamp                                                          
2024-11-16 20:15:00            NaN            NaN            NaN   
2024-11-16 20:30:00            NaN            NaN            NaN   
2024-11-16 20:45:00            NaN            NaN            NaN   
2024-11-16 21:00:00            NaN            NaN            NaN   
2024-11-16 21:15:00            NaN            NaN            NaN   

                     TP_MAX_142560  TP_MIN_142560  TP_MAX_143280  \
timestamp                                                          
2024-11-16 20:15:00            NaN            NaN            NaN   
2024-11-16 20:30:00            NaN            NaN            NaN   
2024-11-16 20:45:00            NaN            NaN            NaN   
2024-11-16 21:00:00            NaN            NaN            NaN   
2024-11-16 21:15:00            NaN            NaN            NaN   

                     TP_MIN_143280  TP_MAX_144000  TP_MIN_144000  
timestamp                                                         
2024-11-16 20:15:00            NaN            NaN            NaN  
2024-11-16 20:30:00            NaN            NaN            NaN  
2024-11-16 20:45:00            NaN            NaN            NaN  
2024-11-16 21:00:00            NaN            NaN            NaN  
2024-11-16 21:15:00            NaN            NaN            NaN  

[5 rows x 794 columns]

In [36]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure with secondary y-axis
fig = make_subplots(rows=2, cols=1, shared_xaxes=True, vertical_spacing=0.03, 
                    subplot_titles=(trading_pair, 'MACD'),
                    row_heights=[0.7, 0.3])

# Add candlestick
fig.add_trace(go.Candlestick(x=candles_df.index,
                             open=candles_df['open'],
                             high=candles_df['high'],
                             low=candles_df['low'],
                             close=candles_df['close'],
                             name='OHLC'),
              row=1, col=1)

# Add EMAs
ema_fast = f'EMA_{ema_short}'
ema_med = f'EMA_{ema_medium}' 
ema_slow = f'EMA_{ema_long}'

fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df[ema_fast],
                         line=dict(color='#00FF00', width=2),
                         name='Fast EMA'), row=1, col=1)
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df[ema_med],
                         line=dict(color='#FFA500', width=2), 
                         name='Medium EMA'), row=1, col=1)
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df[ema_slow],
                         line=dict(color='#0000FF', width=2),
                         name='Slow EMA'), row=1, col=1)

# Add support and resistance TP
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df["support_tp"],
                         line=dict(color='#00FF00', width=2),
                         name='Support TP'), row=1, col=1)
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df["resistance_tp"],
                         line=dict(color='#00FF00', width=2),
                         name='Resistance TP'), row=1, col=1)

# Add support and resistance SL
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df["support_sl"],
                         line=dict(color='#FF0000', width=2),
                         name='Support SL'), row=1, col=1)
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df["resistance_sl"],
                         line=dict(color='#FF0000', width=2),
                         name='Resistance SL'), row=1, col=1)


# # Add ATR support and resistance
# fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df["long_atr_support"],
#                          line=dict(color='#00FF00', width=2),
#                          name='Long ATR Support'), row=1, col=1)
# fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df["short_atr_resistance"],
#                          line=dict(color='#FF0000', width=2),
#                          name='Short ATR Resistance'), row=1, col=1)

# Update layout for dark theme
fig.update_layout(
    title=f'{exchange} - {trading_pair} - {timeframe}',
    width=1200, height=800,
    font=dict(color='#e1e1e1'),
    plot_bgcolor='#1e1e1e',
    paper_bgcolor='#1e1e1e',
    xaxis_rangeslider_visible=False,
    legend=dict(bgcolor='rgba(0,0,0,0)'),
    yaxis=dict(title='Price'),
    yaxis2=dict(title='MACD', showgrid=False),
    showlegend=False
)

# Update axes
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='#323232', zeroline=False)
fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='#323232', zeroline=False)

# Show the plot
fig.show()

In [15]:
# Generate signal


macdh = candles_df[f"MACDh_{macd_fast}_{macd_slow}_{macd_signal}"]
short_ema = candles_df[f"EMA_{ema_short}"]
medium_ema = candles_df[f"EMA_{ema_medium}"]
long_ema = candles_df[f"EMA_{ema_long}"]
close = candles_df["close"]


long_condition = (short_ema > medium_ema) & (medium_ema > long_ema) & (close > short_ema) & (close > candles_df["long_atr_support"]) & (macdh > 0) 
short_condition = (short_ema < medium_ema) & (medium_ema < long_ema) & (close < short_ema) & (close < candles_df["short_atr_resistance"]) & (macdh < 0)

candles_df["signal"] = 0
candles_df.loc[long_condition, "signal"] = 1
candles_df.loc[short_condition, "signal"] = -1

In [16]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

fig = make_subplots(rows=3, cols=1, shared_xaxes=True, vertical_spacing=0.02,
                    subplot_titles=('OHLC with BB', 'MACD', 'Signal'),
                    row_heights=[0.6, 0.2, 0.2])

# Add candlestick
fig.add_trace(go.Candlestick(x=candles_df.index,
                             open=candles_df['open'],
                             high=candles_df['high'],
                             low=candles_df['low'],
                             close=candles_df['close'],
                             name='Candlesticks'),
              row=1, col=1)


# Add EMAs
ema_fast = f'EMA_{ema_short}'
ema_med = f'EMA_{ema_medium}' 
ema_slow = f'EMA_{ema_long}'

fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df[ema_fast],
                         line=dict(color='#00FF00', width=2),
                         name='Fast EMA'), row=1, col=1)
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df[ema_med],
                         line=dict(color='#FFA500', width=2), 
                         name='Medium EMA'), row=1, col=1)
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df[ema_slow],
                         line=dict(color='#0000FF', width=2),
                         name='Slow EMA'), row=1, col=1)

# Add MACD
macd = f'MACD_{macd_fast}_{macd_slow}_{macd_signal}'
macd_s = f'MACDs_{macd_fast}_{macd_slow}_{macd_signal}'
macd_hist = f'MACDh_{macd_fast}_{macd_slow}_{macd_signal}'

fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df[macd], 
                         line=dict(color='#00FFFF', width=2),
                         name='MACD'), row=2, col=1)
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df[macd_s], 
                         line=dict(color='#FFA500', width=2),
                         name='Signal'), row=2, col=1)
fig.add_trace(go.Bar(x=candles_df.index, y=candles_df[macd_hist], name='Histogram',
                     marker_color=candles_df[macd_hist].apply(
                         lambda x: '#00FF00' if x >= 0 else '#FF0000')),
              row=2, col=1)

# Add ATR support and resistance
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df["long_atr_support"],
                         line=dict(color='#00FF00', width=2),
                         name='Long ATR Support'), row=1, col=1)
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df["short_atr_resistance"],
                         line=dict(color='#FF0000', width=2),
                         name='Short ATR Resistance'), row=1, col=1)

# Add the signal line
fig.add_trace(go.Scatter(x=candles_df.index, y=candles_df['signal'],
                         mode='lines',
                         name='Signal',
                         line=dict(color="white")),
              row=3, col=1)

# Update layout for dark theme
fig.update_layout(
    title=f'{exchange} - {trading_pair} - {timeframe}',
    width=1500, height=1000,
    font=dict(color='#e1e1e1'),
    plot_bgcolor='#1e1e1e',
    paper_bgcolor='#1e1e1e',
    xaxis_rangeslider_visible=False,
    legend=dict(bgcolor='rgba(0,0,0,0)'),
    yaxis=dict(title='Price'),
    yaxis2=dict(title='MACD', showgrid=False),
    yaxis3=dict(title='Signal', showgrid=False),
    showlegend=False
)

# Update axes
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='#323232', zeroline=False)
fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='#323232', zeroline=False)

# Show the plot
fig.show()


# CONCLUSION

In this notebook, we have implemented a strategy combining the MACD (Moving Average Convergence Divergence) indicator with Bollinger Bands. We've visualized these indicators along with the price data and generated signals based on their interactions. This approach provides a solid foundation for our trading strategy.
 
## Key components of our strategy include:
 1. MACD for trend identification
 2. Bollinger Bands for volatility measurement and potential reversal points
 3. A signal line derived from the combination of these indicators
 
 The next step is to backtest this strategy to evaluate its profitability and robustness. For this purpose, we have created a controller file named `macd_bb.py` in this folder. This file implements the logic we've developed here, allowing us to conduct comprehensive backtests in the subsequent notebook.